In [ ]:
import base64
import os
import requests
from bs4 import BeautifulSoup
from typing import List, Optional
from pydantic import BaseModel
import openai
from typing import Dict
from agents import Agent, Runner
from dotenv import load_dotenv
from managed_prompt import build_prompt
from image import convert_base64_to_file
from PIL import Image

from datetime import datetime
from image import convert_base64_to_file
from fetch import get_google_image_search_first_result_as_data_uri, get_wikipedia_image_as_data_uri, ExtractCityFeaturesOutput, ExtractedCityFeatures
from llm_structured_city import extract_city_features_via_ai

load_dotenv()

HEADERS = {
    'User-Agent': 'CityscapeCanvas/1.0 (Python Port)'
}



async def extract_city_features(city_name:str) -> ExtractCityFeaturesOutput:
    features = await extract_city_features_via_ai(city_name)    
    wikipedia_image = get_wikipedia_image_as_data_uri(city_name)
    google_image = get_google_image_search_first_result_as_data_uri(city_name)
    satellite_image = get_google_image_search_first_result_as_data_uri(f"{city_name} vue aérienne")
    panorama_image = get_google_image_search_first_result_as_data_uri(f"{city_name} panorama")
    images = [(p, get_google_image_search_first_result_as_data_uri(f'{city_name} - {p}')) for p in features.combinedPointsOfInterest]

    return ExtractCityFeaturesOutput(
        cityName=city_name,
        features=features,
        wikipediaImageUrl=wikipedia_image,
        firstGoogleImageUrl=google_image,
        satelliteImageUrl=satellite_image,
        panoramaImageUrl=panorama_image,
        otherImageUrls= images
    )


def visualize_city_images(city: ExtractCityFeaturesOutput) :
    for image_url in [city.wikipediaImageUrl, city.firstGoogleImageUrl, city.satelliteImageUrl, city.panoramaImageUrl]:
        if image_url:
            image_file = convert_base64_to_file(image_url)
            image = Image.open(image_file)
            image.show()


def generate_poster(prompt:str, city: ExtractCityFeaturesOutput):
    result = openai.images.edit(
        model="gpt-image-1",
        image=
        [
           ("satelliteView.jpg", convert_base64_to_file(city.satelliteImageUrl), "image/jpeg"),
           ("cityView.jpg", convert_base64_to_file(city.firstGoogleImageUrl), "image/jpeg"),
           ("panoramaView.jpg", convert_base64_to_file(city.panoramaImageUrl), "image/jpeg")
        ] +
        [(f"{tuple[0]}.jpg",  convert_base64_to_file(tuple[1]), "image/jpeg") for tuple in city.otherImageUrls
        ],
        prompt=prompt
    )

    image_base64 = result.data[0].b64_json
    image_bytes = base64.b64decode(image_base64)

    #  Save the image to a file
    # Crée le dossier s'il n'existe pas
    folder_path = f"generated/{city.cityName}"
    os.makedirs(folder_path, exist_ok=True)
    with open(f"{folder_path}/poster-{city.cityName}-{datetime.now()}.png", "wb") as f:
        #
            f.write(image_bytes)
        
    return image_bytes


TypeError: Too many parameters for typing.List; actual 2, expected 1

In [2]:
city = await extract_city_features("Curitiba")

prompt = build_prompt(city.features)
visualize_city_images(city)
print(prompt)

NameError: name 'extract_city_features' is not defined

In [5]:
images = [
    # city.satelliteImageUrl,
    # city.wikipediaImageUrl
    # city.firstGoogleImageUrl,
]
generate_poster(city.cityName,prompt,city.satelliteImageUrl , city.panoramaImageUrl, city.wikipediaImageUrl if city.wikipediaImageUrl is not None else city.firstGoogleImageUrl , [image for image in images if image is not None],)

b'\x89PNG\r\n\x1a\n\x00\x00\x00\rIHDR\x00\x00\x04\x00\x00\x00\x06\x00\x08\x02\x00\x00\x00g\xe0\xad\xfd\x00\x017wcaBX\x00\x017wjumb\x00\x00\x00\x1ejumdc2pa\x00\x11\x00\x10\x80\x00\x00\xaa\x008\x9bq\x03c2pa\x00\x00\x007\x13jumb\x00\x00\x00Gjumdc2ma\x00\x11\x00\x10\x80\x00\x00\xaa\x008\x9bq\x03urn:c2pa:9ec227e3-a681-4e29-9b86-7e01f5a2db15\x00\x00\x00\x01\xe1jumb\x00\x00\x00)jumdc2as\x00\x11\x00\x10\x80\x00\x00\xaa\x008\x9bq\x03c2pa.assertions\x00\x00\x00\x01\x05jumb\x00\x00\x00)jumdcbor\x00\x11\x00\x10\x80\x00\x00\xaa\x008\x9bq\x03c2pa.actions.v2\x00\x00\x00\x00\xd4cbor\xa1gactions\x82\xa3factionlc2pa.createdmsoftwareAgent\xbfdnamefGPT-4o\xffqdigitalSourceTypexFhttp://cv.iptc.org/newscodes/digitalsourcetype/trainedAlgorithmicMedia\xa2factionnc2pa.convertedmsoftwareAgent\xbfdnamejOpenAI API\xff\x00\x00\x00\xabjumb\x00\x00\x00(jumdcbor\x00\x11\x00\x10\x80\x00\x00\xaa\x008\x9bq\x03c2pa.hash.data\x00\x00\x00\x00{cbor\xa5jexclusions\x81\xa2estart\x18!flength\x197Ednamenjumbf manifestcalgfsha25

In [6]:
visualize_city_images(city)
